# Understand embeddings with Word2Vec

### Exercise objectives:
- Convert words to vector representations thanks to embeddings
- Discover the powerful Word2Vec algorithm

<hr>
<hr>

_Embeddings_ are representation of words thanks to vectors. These embeddings can be learnt within a Neural Network. But it can take time to converge. Another option is to learn them as a first step. Then, use them directly to feed the word representation into an RNN. 



# The data

Keras provides many datasets, among which the ÌMDB dataset: it corresponds to sentences that are movie reviews. Each of them is related to a score given by the review writer.

❓ **Question** ❓ Let's first load the data. You don't have to understand what is going on in the function, it does not matter here.

⚠️ **Warning** ⚠️ The `load_data` function has a `percentage_of_sentences` argument. Depending on your computer, there are chances that a too large number of sentences will make your compute slow down, or even freeze - your RAM can even overflow. For that reason, **you should start with 10% of the sentences** and see if your computer handles it. Otherwise, rerun with a lower number. 

⚠️ **DISCLAIMER** ⚠️ **No need to play _who has the biggest_ (RAM) !** The idea is to get to run your models quickly to prototype. Even in real life, it is recommended that you start with a subset of your data to loop and debug quickly. So increase the number only if you are into getting the best accuracy. 

In [1]:
###########################################
### Just run this cell to load the data ###
###########################################

import tensorflow_datasets as tfds
from tensorflow.keras.preprocessing.text import text_to_word_sequence

def load_data(percentage_of_sentences=None):
    train_data, test_data = tfds.load(name="imdb_reviews", split=["train", "test"], batch_size=-1, as_supervised=True)

    train_sentences, y_train = tfds.as_numpy(train_data)
    test_sentences, y_test = tfds.as_numpy(test_data)
    
    # Take only a given percentage of the entire data
    if percentage_of_sentences is not None:
        assert(percentage_of_sentences> 0 and percentage_of_sentences<=100)
        
        len_train = int(percentage_of_sentences/100*len(train_sentences))
        train_sentences, y_train = train_sentences[:len_train], y_train[:len_train]
  
        len_test = int(percentage_of_sentences/100*len(test_sentences))
        test_sentences, y_test = test_sentences[:len_test], y_test[:len_test]
    
    X_train = [text_to_word_sequence(_.decode("utf-8")) for _ in train_sentences]
    X_test = [text_to_word_sequence(_.decode("utf-8")) for _ in test_sentences]
    
    return X_train, y_train, X_test, y_test

X_train, y_train, X_test, y_test = load_data(percentage_of_sentences=10)

2021-11-12 11:45:21.673010: I tensorflow/core/platform/cpu_feature_guard.cc:142] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2021-11-12 11:45:21.734447: I tensorflow/compiler/mlir/mlir_graph_optimization_pass.cc:176] None of the MLIR Optimization Passes are enabled (registered 2)


In the previous exercise, we jointly learnt a representation for the words, and feed this representation to a RNN, as shown here : 

<img src="layers_embedding.png" width="400px" />

However, this increases the number of parameters to learn, which can slow the convergence, and make it harder!

For that reason, we will separate the steps of learning the word representation and feeding it to a RNN. As shown here : 

<img src="word2vec_representation.png" width="400px" />

We will learn the embedding with the word2vec.

The drawback is indeed that the learnt embedding is not _specifically_ designed for our task. However, learning it independently of the task at hand (sentiment analysis) has some advantages : 
- it is very fast to do in general (with word2vec)
- the representation learnt by word2vec is still meaningful 
- the convergence of the RNN alone will be easier and faster

So let's learn an embedding with word2vec and see how meaningful it is!


# Embedding with Word2Vec

Let's use Word2Vec to embed the words of our sentences. Word2Vec will be able to convert each word to a fixed-size vectorial representation.

For instance, we will have:
- 'dog' --> [0.1, -0.3, 0.8]
- 'cat' --> [-1.1, 2.3, 0.7]
- 'apple' --> [3.1, 0.9, -4.7]

Here, your embedding space is of size 3.

What you expect is to have representation such as words with close meanings are close in this embedding space. As on this example:

![Embedding](word_embedding.png)

❓ **Question** ❓ Let's run Word2Vec! The following code imports word2vec from [GENSIM](https://radimrehurek.com/gensim/), a great python package that makes the use of the word2vec algorithm easy, fast and accurate - which is not an easy task. The second line learns the embedding representation of the words thanks to the sentences in `X_train`.

In [2]:
from gensim.models import Word2Vec

word2vec = Word2Vec(sentences=X_train)

Let's look at the embedded representation of some words.

You can use `word2vec.wv` as a dictionary.
For instance, `word2vec.wv['dog']` will return a representation of `dog` in the embedding space.

❓ **Question** ❓ Try different words - especially, try non-existing words to see that they don't have any representation (which is perfectly normal as their representation were not learn). 

In [9]:
# YOUR CODE HERE
word2vec.wv['love']

array([ 0.12046   , -0.31686482, -0.10011765,  0.18921675, -0.3078854 ,
       -1.0515816 , -0.11123053,  1.1701874 , -0.08435415, -0.49289748,
       -0.8571922 , -0.51707095, -0.55345523,  0.47241187, -0.04347182,
       -0.2410871 ,  0.5452925 , -0.22875625,  0.36128634, -0.46602017,
        0.2574179 ,  0.4557974 , -0.13931653, -0.08330563, -0.31118503,
        0.20047428, -0.48539582, -0.24793199, -0.32922646,  0.36204317,
        0.4892166 ,  0.20496014, -0.00523067, -0.61516   , -0.41727632,
        0.88497865,  0.2559    ,  0.01758081, -0.46219996, -0.3594725 ,
       -0.07090484,  0.25470772,  0.3999101 ,  0.27883118,  0.1846159 ,
        0.00407536, -0.3481901 , -0.31442857,  0.6488042 ,  0.05358575,
        0.02325928, -0.5134924 ,  0.3059785 , -0.15305232,  0.25405547,
        0.47093764,  0.25820038, -0.17234607, -0.61608595,  0.20637465,
        0.10157074,  0.3818678 , -0.4261106 ,  0.42964098, -0.42786053,
        0.13334773,  0.4187363 ,  0.17887005, -0.57836896,  0.85

In [11]:
word2vec.wv['hello']

array([-0.0717152 ,  0.09223792, -0.01300832,  0.0986893 ,  0.00622321,
       -0.11056335,  0.06485566,  0.28077587, -0.08129767, -0.09710858,
       -0.06115176, -0.15886831, -0.00413972,  0.06028856,  0.01846912,
       -0.06262588,  0.050731  , -0.06734473, -0.03392933, -0.17424393,
        0.0517903 ,  0.03997524,  0.10720462, -0.0802027 ,  0.01704365,
        0.02337438, -0.0861527 , -0.05889701, -0.09835906, -0.02157541,
        0.12575433, -0.00186169,  0.02411787, -0.16117735, -0.05924848,
        0.10306492,  0.09723591, -0.01616414, -0.0624132 , -0.12652554,
       -0.06707861, -0.10077894, -0.07503995,  0.09292893,  0.1492006 ,
       -0.01744463, -0.04078352, -0.04978814,  0.09198689,  0.07109889,
        0.05945846, -0.15783216, -0.10242204, -0.03026658, -0.15085392,
        0.12832539,  0.07542612,  0.02474115, -0.07629142,  0.02735331,
        0.0770016 ,  0.01101051, -0.00724542,  0.03563347, -0.10798445,
        0.12598488, -0.0356255 ,  0.05452936, -0.19472107,  0.11

❓ **Question** ❓ What is the size of each word representation, and therefore, what is the size of the embedding space?

In [12]:
# YOUR CODE HERE
word2vec.wv['hello'].size
#the size of representation of the word hello is 100

100

How to know if this embedding make any sense? To do that, we will check that words with a close meaning have close representations. 

Let's use the `word2vec.most_similar(...)` method that, given an input word, display the "closest" words in the embedding space. If the embedding is well done, then words that have close meanings will have close representation in the embedding space.

❓ **Question** ❓ Test the `most_similar` method on different words. 

❗ **Remark** ❗ Indeed, the quality of the closeness will depend on the quality of your embedding, and thus, depend on the number of sentences that you have loaded and from which you create your embedding.

In [18]:
# YOUR CODE HERE
word2vec.wv.most_similar('sun', topn=10)

[('usa', 0.9831674098968506),
 ('immediately', 0.9804306030273438),
 ('midnight', 0.9786336421966553),
 ('portuguese', 0.9783303737640381),
 ('yard', 0.9781579375267029),
 ('broke', 0.9768943190574646),
 ('web', 0.9767166972160339),
 ('system', 0.9753734469413757),
 ('glory', 0.9753053188323975),
 ('pictures', 0.975010335445404)]

In [32]:
word2vec.wv.most_similar('horse', topn=10)

[('soldier', 0.985224723815918),
 ('trail', 0.9842843413352966),
 ('fat', 0.9842828512191772),
 ('suit', 0.9840371608734131),
 ('dude', 0.9837394952774048),
 ('gas', 0.9835934042930603),
 ('photo', 0.9835307598114014),
 ('harris', 0.9833290576934814),
 ('ann', 0.9831459522247314),
 ('force', 0.9828765392303467)]

Similarly to `most_similar` used on words directly, we can use `similar_by_vector` on vectors to do the same thing :

In [21]:
# YOUR CODE HERE
#similar by vectors corresponds to the vectorial embedding of a given word
v_queen = word2vec.wv['queen']
v_king = word2vec.wv['king']
v_man = word2vec.wv['man']

v_result = v_queen - v_king + v_man

word2vec.wv.similar_by_vector(v_result)


[('man', 0.9792605638504028),
 ('girl', 0.9447348713874817),
 ('woman', 0.9388829469680786),
 ('wife', 0.8794184327125549),
 ('guy', 0.8610104918479919),
 ('emy', 0.8483206033706665),
 ('father', 0.8478241562843323),
 ('role', 0.8456472754478455),
 ('young', 0.8415295481681824),
 ('husband', 0.8334589600563049)]

# Arithmetic on words

Now, let's do mathematical operations on words - meaning on their vector representations!

As any word is represented as a vector, you can do basic arithmetic as:

$$W2V(good) - W2V(bad)$$

❓ **Question** ❓ Do this mathematical operation and print the result

In [ ]:
from gensim.models import Word2Vec

In [29]:
# YOUR CODE HERE
word2vec = Word2Vec(sentences=X_train[:10000], vector_size=30, window=2, min_count=10)

v_good = word2vec.wv['good']
v_bad = word2vec.wv['bad']
v_result = v_good - v_bad

word2vec.wv.similar_by_vector(v_result)


[('have', 0.28345414996147156),
 ("i've", 0.2783639132976532),
 ('with', 0.2660048305988312),
 ('ever', 0.25416499376296997),
 ('a', 0.23221991956233978),
 ('never', 0.2207319587469101),
 ('good', 0.21914483606815338),
 ('has', 0.21113693714141846),
 ('given', 0.21100150048732758),
 ('been', 0.19276507198810577)]

Now, image for a second that, somehow, the following equality holds true - just for a second

$$W2V(good) - W2V(bad) = W2V(nice) - W2V(stupid)$$

which is equivalent to 

$$W2V(good) - W2V(bad) + W2V(stupid) = W2V(nice)$$

❓ **Question** ❓ Let's, just for fun (as it would be foolish of us to think that this equality holds true ...), do the operation $W2V(good) - W2V(bad) + W2V(stupid)$ and store it in a `res` variable (which will be a vector of size 100 that you can print).

In [27]:
# YOUR CODE HERE
#2eme équation
word2vec = Word2Vec(sentences=X_train[:10000], vector_size=30, window=2, min_count=10)

v_good = word2vec.wv['good']
v_bad = word2vec.wv['bad']
v_nice = word2vec.wv['nice']
v_stupid = word2vec.wv['stupid']
v_result = v_good - v_bad + v_stupid

word2vec.wv.similar_by_vector(v_result)

[('good', 0.8462859988212585),
 ('decent', 0.7936821579933167),
 ('nice', 0.7640626430511475),
 ('great', 0.7475048303604126),
 ('fine', 0.6963610649108887),
 ('scary', 0.6720144152641296),
 ('interesting', 0.6696817874908447),
 ('poor', 0.6682125926017761),
 ('presented', 0.666771650314331),
 ('confusing', 0.6640083193778992)]

In [35]:
#une seule équation
word2vec = Word2Vec(sentences=X_train[:10000], vector_size=10, window=2, min_count=10)

v_good = word2vec.wv['good']
v_bad = word2vec.wv['bad']

v_result = v_good - v_bad

word2vec.wv.similar_by_vector(v_result)

[('into', 0.49754127860069275),
 ('by', 0.46784287691116333),
 ('between', 0.4085288345813751),
 ('on', 0.3938261568546295),
 ('with', 0.388333261013031),
 ('new', 0.3780258297920227),
 ('from', 0.3689729571342468),
 ('in', 0.34808170795440674),
 ('at', 0.3240007162094116),
 ('of', 0.3168128430843353)]

We earlier said that, for any vector, it is possible to see the closest vectors in the embedding space.

❓ **Question** ❓ Look at the closest vector (thanks to the `word2vec.wv.similar_by_vector` function) of `res`

In [36]:
# YOUR CODE HERE
#voir plus haut !

<bound method KeyedVectors.similar_by_vector of <gensim.models.keyedvectors.KeyedVectors object at 0x16105b490>>

Incredible right! You can do arithmetic operations on words!

❓ **Question** ❓ You can try on arithmetic such as 

$$W2V(Boy) - W2V(Girl) = W2V(Man) - W2V(Woman)$$

or 

$$W2V(Queen) - W2V(King) = W2V(actress) - W2V(actor)$$

❗ **Remark** ❗ You will probably see that the results are not perfect. But don't forget that you trained your model on a very small corpus.

In [38]:
# YOUR CODE HERE
word2vec = Word2Vec(sentences=X_train[:10000], vector_size=30, window=2, min_count=10)

v_boy = word2vec.wv['boy']
v_girl = word2vec.wv['girl']
v_man = word2vec.wv['man']
v_woman = word2vec.wv['woman']
v_result = v_boy - v_girl 
v_result1 = v_man - v_woman


In [39]:
word2vec.wv.similar_by_vector(v_result)

[('10', 0.6329420804977417),
 ('2', 0.5563251972198486),
 ('1', 0.545638382434845),
 ('3', 0.5450170040130615),
 ('4', 0.5073962807655334),
 ('5', 0.4991835355758667),
 ('7', 0.4563124477863312),
 ('9', 0.44511836767196655),
 ('my', 0.44110119342803955),
 ('last', 0.4341210424900055)]

In [40]:
word2vec.wv.similar_by_vector(v_result1)

[('an', 0.3709912598133087),
 ('man', 0.3636116683483124),
 ('black', 0.27787795662879944),
 ('between', 0.26757946610450745),
 ('main', 0.2599886953830719),
 ('young', 0.25393256545066833),
 ('has', 0.25206178426742554),
 ('plays', 0.24611946940422058),
 ('rather', 0.2436242252588272),
 ('development', 0.2334667146205902)]

You might wonder where does this magic comes from (at quite a low price, you just run a line of code on a very small corpus and it was trained within few minutes). The magic comes from the way Word2Vec is trained. The details are quite complex, but you can remember that Word2vec, in `word2vec = Word2Vec(sentences=X_train)` , actually trains a internal neural network (that you don't see).  

In a nutshell, this internal NN predicts a word from the surroundings words in a sentences. So it chooses many splits in the different sentences, choose some words as inputs $X$  and a word as output $y$ which it tries to predict, in the embedding space.

And as any neural network, Word2Vec has some hyperparameters. Let's check some. 


# Word2Vec hyperparameters


❓ **Question** ❓ The first important hyperparameter is the `vector_size` argument. It corresponds to the size of the embedding space. Learn a new `word2vec_2` model, still trained on the `X_train`, but with a smaller or higher `vector_size`.

Verify on some words that the corresponding embedding is of your selected size.

In [41]:
# YOUR CODE HERE
word2vec = Word2Vec(sentences=X_train[:1000], vector_size=100, min_count=5) 

❓ **Question** ❓ Use the `word2vec.wv.key_to_index` attribute to display the size of the learnt vocabulary. On the other hand, compare it to the number of different words in `X_train`.

In [46]:
# YOUR CODE HERE
#word2vec.wv.key_to_index is a dictionnary
len(word2vec.wv.key_to_index) 

4054

In [50]:
len(X_train)

2500

There is an important difference between the number of words in the train sentences and in the Word2Vec vocabulary, even though it has been train on the train sentence set. The reasons comes from the second important hyperparameter of Word2Vec :  `min_count`. 

`min_count` is a integer that tells you how many occurences a given word should have to be learn in the embedding space. For instance, let's say that the word "movie" appears 1000 times in the corpus and "simba" only 2 times. If `min_count=3`, the word "simba" will be skipped during the training.

The intention is to have only words that are sufficiently present in the corpus to have a robust embedded representation

❓ **Question** ❓ Learn a new `word2vec_3` model with a `min_count` higher than 5 (which is the default value) and a `word2vec_4` with a `min_count` smaller than 5, and then, compare the size of the vocabulary for all the different word2vec that you have trained (you can choose any `vector_size` you want).

In [56]:
# YOUR CODE HERE
word2vec_3 = Word2Vec(sentences=X_train[:1000], vector_size=100,window=5, min_count=7) 
len(word2vec_3.wv.key_to_index) 

2997

In [57]:
word2vec_4 = Word2Vec(sentences=X_train[:1000], vector_size=100,window=5, min_count=3) 
len(word2vec_4.wv.key_to_index)
#the size of the vocabulary is bigger when the min count is smaller 

6479

Remember that we say that word2vec has an internal neural network that it optimizes based on some predictions? These predictions actually correspond to predicting a word based on surrounding words. The surroundings words are in a `window` which corresponds to the number of words taken into account. And you can train the word2vec with different `window` sizes.

❓ **Question** ❓ Learn a new `word2vec_5` model with a `window` different than previously (default is 5).

In [61]:
# YOUR CODE HERE
word2vec_5 = Word2Vec(sentences=X_train[:1000], vector_size=100, window=10, min_count=3)
len(word2vec_5.wv.key_to_index)

6479

The arguments you have seen (`vector_size`, `min_count` and `window`) are usually the one that you should start changing to get a better performance for your model.

But you can also look at other arguments in the [documentation](https://radimrehurek.com/gensim/models/word2vec.html#gensim.models.word2vec.Text8Corpus)



# Convert our train and test set to RNN ready data

Remember that word2vec is the first step to the overall process of feeding such a representation into a RNN, as shown here :

<img src="word2vec_representation.png" width="400px" />



Now, let's work on Step 2 by converting the training and test data into their vector representation to be ready to be feed in RNNs.

❓ **Question** ❓ Now, write a function that, given a sentence, returns a matrix that corresponds to the embedding of the full sentence, which means that you have to embed each word one after the other and concatenate the result to output a 2D matrix (be sure that your output is a NumPy array)

❗ **Remark** ❗ You will probably notice that some words you are trying to convert throw errors as they are said not to belong to the dictionary:

- for the test set, this is understandable: some words were not in the train set and thus their embedded representation is unknown
- for the train set, due to `min_count` hyperparameter, not all the words have a vector representation

In any case, just skip the missing words here.

In [62]:
X_train

[['this',
  'was',
  'an',
  'absolutely',
  'terrible',
  'movie',
  "don't",
  'be',
  'lured',
  'in',
  'by',
  'christopher',
  'walken',
  'or',
  'michael',
  'ironside',
  'both',
  'are',
  'great',
  'actors',
  'but',
  'this',
  'must',
  'simply',
  'be',
  'their',
  'worst',
  'role',
  'in',
  'history',
  'even',
  'their',
  'great',
  'acting',
  'could',
  'not',
  'redeem',
  'this',
  "movie's",
  'ridiculous',
  'storyline',
  'this',
  'movie',
  'is',
  'an',
  'early',
  'nineties',
  'us',
  'propaganda',
  'piece',
  'the',
  'most',
  'pathetic',
  'scenes',
  'were',
  'those',
  'when',
  'the',
  'columbian',
  'rebels',
  'were',
  'making',
  'their',
  'cases',
  'for',
  'revolutions',
  'maria',
  'conchita',
  'alonso',
  'appeared',
  'phony',
  'and',
  'her',
  'pseudo',
  'love',
  'affair',
  'with',
  'walken',
  'was',
  'nothing',
  'but',
  'a',
  'pathetic',
  'emotional',
  'plug',
  'in',
  'a',
  'movie',
  'that',
  'was',
  'devoid',

In [66]:
np.empty([8, 8])

array([[0.00000000e+000, 0.00000000e+000, 1.58101007e-322,
        0.00000000e+000, 0.00000000e+000, 0.00000000e+000,
        0.00000000e+000, 0.00000000e+000],
       [0.00000000e+000, 0.00000000e+000, 0.00000000e+000,
        0.00000000e+000, 9.69156351e-268, 0.00000000e+000,
        0.00000000e+000, 0.00000000e+000],
       [0.00000000e+000, 0.00000000e+000, 0.00000000e+000,
        0.00000000e+000, 0.00000000e+000, 0.00000000e+000,
        0.00000000e+000, 0.00000000e+000],
       [0.00000000e+000, 0.00000000e+000, 0.00000000e+000,
        0.00000000e+000, 0.00000000e+000, 0.00000000e+000,
        0.00000000e+000, 0.00000000e+000],
       [0.00000000e+000, 0.00000000e+000, 0.00000000e+000,
        0.00000000e+000, 0.00000000e+000, 0.00000000e+000,
        0.00000000e+000, 0.00000000e+000],
       [0.00000000e+000, 0.00000000e+000, 0.00000000e+000,
        0.00000000e+000, 0.00000000e+000, 0.00000000e+000,
        0.00000000e+000, 0.00000000e+000],
       [0.00000000e+000, 0.0000000

In [87]:
import numpy as np
from tensorflow.keras.preprocessing.text import text_to_word_sequence
example = ['this', 'movie', 'is', 'the', 'worst', 'action', 'movie', 'ever']
example_missing_words = ['this', 'movie', 'is', 'laaaaaaaaaame']


def embed_sentence(word2vec, sentence):
    embedded_sentence = []
    for word in sentence:
        if word in word2vec.wv:
            #embedded_sentence= np.vstack([embedded_sentence,word2vec.wv[word]]) 
            embedded_sentence.append(word2vec.wv[word])
    return np.array(embedded_sentence)
     # YOUR CODE HERE

### Checks
embedded_sentence = embed_sentence(word2vec, example)
assert(type(embedded_sentence) == np.ndarray)
assert(embedded_sentence.shape == (8, 100))

embedded_sentence_missing_words = embed_sentence(word2vec, example_missing_words)  
assert(type(embedded_sentence_missing_words) == np.ndarray)
assert(embedded_sentence_missing_words.shape == (3, 100))

In [69]:
word2vec.wv[example[3]]

array([ 0.36124727,  0.31709445,  0.58896405, -0.05945908, -0.24963948,
       -0.53103876,  0.5949146 ,  1.328424  , -0.80327404, -0.5913224 ,
       -0.08142769, -0.53143764, -0.4250693 ,  0.4926686 ,  0.276741  ,
       -0.10668566,  0.6415829 ,  0.29082757, -1.3124809 , -1.1928757 ,
        0.9009809 , -0.18610947,  0.76081717, -0.45946547,  0.17419353,
        0.30690333, -0.40670872, -0.5539613 , -0.7560896 ,  0.54615974,
        0.00301381,  0.7222418 ,  0.46153408, -1.4376739 ,  0.09376317,
        0.2124565 ,  0.5980806 , -0.70616716, -1.2977518 , -1.2217581 ,
       -0.05157169, -0.3085537 , -0.05998489, -0.47753918,  0.21338712,
       -0.20829323, -0.06105293, -0.2205458 ,  0.5839818 ,  0.9937777 ,
       -0.3768784 , -0.94166327, -0.6671646 , -0.5434858 , -0.6609914 ,
       -0.57986104,  0.20304629,  0.00320744, -0.37678248,  0.4652343 ,
        0.4963096 , -0.14458863,  0.05177453,  0.5214824 , -0.5759039 ,
        0.7516295 , -0.16696264,  0.7033753 , -0.64716095,  0.41

❓ **Question** ❓ Write a function that, given a list of sentence (each sentence being a list of words/strings), returns a list of embedded sentences (each sentence is a matrix). Apply this function to the train and test sentences

Hint: Use the previous function `embed_sentence`

In [72]:
def embedding(word2vec, sentences):
    embed = []
    
    for sentence in sentences:
        embedded_sentence = embed_sentence(word2vec, sentence)
        embed.append(embedded_sentence)
        
    return embed
X_train = embedding(word2vec, X_train)
X_test = embedding(word2vec, X_test)

❓ **Question** ❓ In order to have ready-to-use data, do not forget to pad them in order to have tensors that can be divided in batch sizes during the optimization. Store the padedd values in `X_train_pad` and `X_test_pad`. Do not forget the important arguments of the padding ;)

In [ ]:
### YOUR CODE HERE

assert(len(X_train_pad.shape) == 3)
assert(len(X_test_pad.shape) == 3)
assert(X_train_pad.shape[2] == 100)
assert(X_test_pad.shape[2] == 100)